### Imports & Env Setup

In [1]:
%reload_ext autoreload
%autoreload 2
import sys
import os
from dotenv import load_dotenv
load_dotenv()
from datasets import load_dataset

import dspy
sys.path.append(os.path.abspath('../'))
from benchmarks import llama_mmlu_pro, leaderboard_mmlu_pro

/home/justinai/.conda/envs/prompt-migration/lib/python3.10/site-packages/pydantic/_internal/_config.py:345: UserWarning: Valid config keys have changed in V2:
* 'fields' has been removed
  warnings.warn(message, UserWarning)


### Configuration

In [5]:
NUM_THREADS = 48

FEW_SHOTS = 5

# See https://docs.litellm.ai/docs/providers/vllm for details
TASK_MODEL = dspy.LM(
    "hosted_vllm/meta-llama/Llama-3.3-70B-Instruct",
    api_base = 'http://localhost:8000/v1' , # or api_base ?
    # api_version: Optional[str] = None,
    # api_key: Optional[str] = None,
    # seed: Optional[int] = None,
    # max_tokens: Optional[int] = None,
    # timeout: Optional[Union[float, int]] = None,
)
PROMPT_MODEL = dspy.LM(
    "hosted_vllm/meta-llama/Llama-3.3-70B-Instruct",
    api_base = 'http://localhost:8000/v1', # or api_base ?
    # api_version: Optional[str] = None,
    # api_key: Optional[str] = None,
    # seed: Optional[int] = None,
    # max_tokens: Optional[int] = None,
    # timeout: Optional[Union[float, int]] = None,
)

dspy.configure(lm=TASK_MODEL)

# replace this with llama_mmlu_pro or whatever
benchmark = llama_mmlu_pro

# Without chain of thought:
# program = dspy.Predict(
#     benchmark.signature("")
# )

# With chain of thought:
program = dspy.ChainOfThought(
    benchmark.signature("You are a helpful assistant designed to help with multiple choice question.") # put your initial system prompt here, or leave blank
)

evaluate = dspy.Evaluate(
    devset=[],
    max_errors = 500,
    metric=benchmark.metric,
    num_threads=NUM_THREADS,
    display_progress=True,
    display_table=True,
    return_all_scores=True,
    return_outputs=True,
)

### Load dataset

In [6]:
trainset, valset, testset = benchmark.datasets(
    train_size=0.1,
    validation_size=0.2,
)

len(trainset), len(valset), len(testset)

(1197, 2156, 8626)

In [7]:
dataset = load_dataset(
    "meta-llama/Llama-3.3-70B-Instruct-evals",
    "Llama-3.3-70B-Instruct-evals__mmlu_pro__details",
)
full_dataset = list(map(benchmark._task_doc_example, dataset["latest"]))

len(full_dataset)

11979

### Baseline Benchmark

In [13]:
%%time
print("BASE PROMPT:\n", program.predict.signature.instructions)

BASE PROMPT:
 You are a helpful assistant designed to help with multiple choice question.
CPU times: user 97 μs, sys: 0 ns, total: 97 μs
Wall time: 210 μs


In [8]:
%%time

print("Starting execution...")
# eval_subset_size = len(testset)
score, results, all_scores = evaluate(
    program,
    devset=full_dataset,
)

Starting execution...


2025/01/22 10:49:04 ERROR dspy.utils.parallelizer: Error processing item Example({'question': 'Calculate the pH of a 0.10 M solution of sodium acetate, NaOAc. The equilibrium constant for the dissociation of acetic acid is 1.8 × 10^-5.', 'options': {'A': '8.9', 'B': '4.8', 'C': '3.9', 'D': '11.2', 'E': '7.5', 'F': '10.1', 'G': '5.3', 'H': '9.3', 'I': '6.2', 'J': '9.7'}, 'answer': 'A'}) (input_keys={'question', 'options'}): Expected dict_keys(['reasoning', 'answer']) but got dict_keys(['reasoning']). Set `provide_traceback=True` to see the stack trace.
2025/01/22 10:49:05 ERROR dspy.utils.parallelizer: Error processing item Example({'question': "Use the Runge-Kutta method with $h=0.1$ to find approximate values for the solution of the initial value problem $y' + 2y = x^3e^{-2x}$ with y(0)=1 at $x=0.2$.", 'options': {'A': '0.6423', 'B': '0.5987', 'C': '0.6534', 'D': '0.7012', 'E': '0.7891', 'F': '0.6245', 'G': '0.6705', 'H': '0.7123', 'I': '0.5809', 'J': '0.5607'}, 'answer': ''}) (input_

Average Metric: 712.00 / 945 (75.3%):   8%|███                                    | 954/11979 [00:08<02:41, 68.29it/s]

2025/01/22 10:49:16 ERROR dspy.utils.parallelizer: Error processing item Example({'question': 'An interferometer illuminated with red light from cadmium (\\lambda = 6438 A) is used to measure the distance between two points. Calculate this distance, D, if 120 minima pass the reference mark as the mirror is moved from one of thepoints to the other.', 'options': {'A': '0.00589 cm', 'B': '0.00832 cm', 'C': '0.00647 cm', 'D': '0.00773 cm', 'E': '0.00876 cm', 'F': '0.00700 cm', 'G': '0.00912 cm', 'H': '0.01158 cm', 'I': '0.01024 cm', 'J': '0.00456 cm'}, 'answer': 'B'}) (input_keys={'question', 'options'}): Expected dict_keys(['reasoning', 'answer']) but got dict_keys(['reasoning']). Set `provide_traceback=True` to see the stack trace.


Average Metric: 890.00 / 1197 (74.4%):  10%|███▋                                 | 1207/11979 [00:20<05:05, 35.26it/s]

...

Average Metric: 8708.00 / 11840 (73.5%): 100%|██████████████████████████████████| 11979/11979 [10:27<00:00, 19.08it/s]

2025/01/22 10:59:36 INFO dspy.evaluate.evaluate: Average Metric: 8708.0 / 11979 (72.7%)


question  \
0       Which of the following is not one of the potentially negative con...   
1                           Solve the equation 1.2 = 0.4y using mental math.   
2      We must assume that he is a Communist, because he says that he is ...   
3      When a spinning system contracts in the absence of an external tor...   
4      What is the maximum efficiency of a steam engine if the temperatur...   
...                                                                      ...   
11974  Each of the following is a step taken by a therapist who is employ...   
11975  This question refers to the following information. "But you, my de...   
11976  A recent law school graduate took and passed the bar examination. ...   
11977  LC oscillators are used for produce a waveform with frequency rang...   
11978  A 50-hp, 500-volt shunt motor draws a line current of 4.5 amperes ...   

                                                                     options  \
0      {'A': 'the execution of innocent persons', 'B': 'the diminishing o...   
1      {'A': '3', 'B': '−3', 'C': '0.8', 'D': '2', 'E': '0.3', 'F': '5', ...   
2      {'A': 'Argument from Ignorance', 'B': 'Affirming the Consequent', ...   
3      {'A': 'halves', 'B': 'doubles', 'C': 'is transferred to linear mom...   
4      {'A': '25%', 'B': '18.5%', 'C': '20%', 'D': '15%', 'E': '27.9%', '...   
...                                                                      ...   
11974  {'A': 'having the client confront the actual feared object or situ...   
11975  {'A': 'a people without a strong central authority are doomed to l...   
11976  {'A': 'constitutional, because it safeguards the principle of reha...   
11977  {'A': '1 kHz to 100 kHz', 'B': '500 MHz to 1 GHz', 'C': '1 Hz to 1...   
11978  {'A': '83.70%, 47.85 hp', 'B': '86.50%, 49.00 hp', 'C': '90.55%, 5...   

      example_answer  \
0                  I   
1                  A   
2                  D   
3                  D   
4                  G   
...              ...   
11974              A   
11975              J   
11976              A   
11977              E   
11978              H   

                                                                   reasoning  \
0      To determine which of the following is not one of the potentially ...   
1      To solve the equation 1.2 = 0.4y using mental math, we need to iso...   
2      The given statement assumes that because a person denies being a C...   
3      The question involves understanding the principle of conservation ...   
4      To find the maximum efficiency of a steam engine, we use the Carno...   
...                                                                      ...   
11974  Systematic desensitization is a behavioral technique used to treat...   
11975  The statement "everything always happens for the best" reflects th...   
11976  The state statute regarding the sealing of juvenile records is des...   
11977  LC oscillators, also known as tank circuits or resonant circuits, ...   
11978  To find the horsepower output and efficiency of the shunt motor, w...   

      pred_answer     metric answer  
0               I  ✔️ [True]    NaN  
1               A  ✔️ [True]    NaN  
2               A               NaN  
3               D  ✔️ [True]    NaN  
4               G  ✔️ [True]    NaN  
...           ...        ...    ...  
11974           A  ✔️ [True]    NaN  
11975           J  ✔️ [True]    NaN  
11976           B               NaN  
11977           D               NaN  
11978           D               NaN  

[11979 rows x 7 columns]

CPU times: user 3min 51s, sys: 11 s, total: 4min 2s
Wall time: 10min 31s


(72.69,
 [(Example({'question': ' Which of the following is not one of the potentially negative consequences of imposing the death penalty?', 'options': {'A': 'the execution of innocent persons', 'B': 'the diminishing of state moral authority', 'C': 'the creation of martyrs', 'D': 'the inequality of application across social classes', 'E': 'the incitement effect', 'F': 'the emotional trauma for the executioners', 'G': 'the promotion of a culture of violence', 'H': 'great financial cost', 'I': 'the prevention of future murders', 'J': None}, 'answer': 'I'}) (input_keys={'question', 'options'}),
   Prediction(
       reasoning='To determine which of the following is not one of the potentially negative consequences of imposing the death penalty, we need to analyze each option given. Options A through H and G describe various negative outcomes that can be associated with the death penalty, such as executing innocent people, diminishing state moral authority, creating martyrs, unequal applic

In [5]:
%%time

print("Starting execution...")
evaluate(
    program,
    devset=testset,
)

Starting execution...
Average Metric: 202.00 / 260 (77.7%):   3%|█▏                                      | 259/8626 [00:50<29:49,  4.68it/s]

2025/01/22 09:33:20 ERROR dspy.utils.parallelizer: Error processing item Example({'question': 'Find the minimum of $f(x,y)=2x - 5y$, subject to the constraint $x^2+y^2=144$.', 'options': {'A': '50', 'B': '-64.62', 'C': '144', 'D': '200', 'E': '0', 'F': '-72', 'G': '72', 'H': '-50', 'I': '-200', 'J': '-144'}, 'answer': ''}) (input_keys={'question', 'options'}): Expected dict_keys(['reasoning', 'answer']) but got dict_keys(['reasoning']). Set `provide_traceback=True` to see the stack trace.


Average Metric: 294.00 / 387 (76.0%):   4%|█▊                                      | 387/8626 [01:21<34:15,  4.01it/s]

2025/01/22 09:33:50 ERROR dspy.utils.parallelizer: Error processing item Example({'question': 'What is $(\\frac{1 + cos(2x) + i*sin(2x)}{1 + cos(2x) - i*sin(2x)})^30$ with $x = \\pi / 60$?', 'options': {'A': '-2.0', 'B': '0.0', 'C': '2i', 'D': 'i', 'E': '-1.0', 'F': '0.5', 'G': '-i', 'H': '2.0', 'I': '1.0', 'J': '-0.5'}, 'answer': ''}) (input_keys={'question', 'options'}): Expected dict_keys(['reasoning', 'answer']) but got dict_keys(['reasoning']). Set `provide_traceback=True` to see the stack trace.


Average Metric: 310.00 / 407 (76.2%):   5%|█▉                                      | 409/8626 [01:26<25:20,  5.40it/s]

...

Average Metric: 6285.00 / 8523 (73.7%): 100%|█████████████████████████████████████| 8626/8626 [30:41<00:00,  4.68it/s]

2025/01/22 10:03:11 INFO dspy.evaluate.evaluate: Average Metric: 6285.0 / 8626 (72.9%)


question  \
0     A 50-year-old nurse who had been fired from his job at ahospital t...   
1     Child abuse and neglect are most associated with which of the foll...   
2     One pound of a gas in a piston cylinder arrangement undergoes comp...   
3     A defendant and his friend were down on their luck. They decided t...   
4     Suppose that we are interested in testing the null hypothesis that...   
...                                                                     ...   
8621  One's ability to make inferences about the behavior of a populatio...   
8622                     What is the quotient for the expression 2,314 / 4?   
8623  The part of the neuron that directs synthesis of neurotransmitters...   
8624  The least common multiple of two integers is 240, and the greatest...   
8625  In garden peas, the allele for tall plants (D) is completely domin...   

                                                                    options  \
0     {'A': 'No, because sanctions are not proper against the attorney o...   
1     {'A': 'secure/engaged', 'B': 'disorganized/disoriented', 'C': 'dis...   
2     {'A': '15.54 ft^3/lbm', 'B': '345280 ftlbf/lbm', 'C': '260280 ftlb...   
3     {'A': 'guilty of felony murder.', 'B': 'not guilty, because the cl...   
4     {'A': 'The test statistic will follow a chi-squared distribution w...   
...                                                                     ...   
8621  {'A': 'reliability', 'B': 'face validity', 'C': 'internal validity...   
8622  {'A': '508 r1', 'B': '578 r2', 'C': '578 r1', 'D': '509', 'E': '57...   
8623  {'A': 'axon terminal', 'B': 'axon', 'C': 'synaptic cleft', 'D': 'n...   
8624  {'A': '72', 'B': '1', 'C': '120', 'D': '20', 'E': '240', 'F': '80'...   
8625  {'A': 'All dwarf white', 'B': '1 tall violet: 2 tall white: 1 dwar...   

     example_answer  \
0                 H   
1                 B   
2                 I   
3                 D   
4                 C   
...             ...   
8621              D   
8622              C   
8623              G   
8624              C   
8625              C   

                                                                  reasoning  \
0     The court is likely to grant the hospital's motion for sanctions b...   
1     Child abuse and neglect are most closely associated with a specifi...   
2     To solve this problem, we first need to understand the given condi...   
3     The defendant can be found guilty of his friend's death under the ...   
4     To determine which of the statements are true, let's analyze each ...   
...                                                                     ...   
8621  To answer this question, we need to understand the concept of maki...   
8622  To find the quotient for the expression 2,314 / 4, we need to perf...   
8623  The question asks for the part of the neuron responsible for direc...   
8624  To find the other integer, we can use the relationship between the...   
8625  To solve this, we first need to understand the genotypes and pheno...   

     pred_answer     metric answer  
0              I               NaN  
1              B  ✔️ [True]    NaN  
2              I  ✔️ [True]    NaN  
3              D  ✔️ [True]    NaN  
4              C  ✔️ [True]    NaN  
...          ...        ...    ...  
8621           D  ✔️ [True]    NaN  
8622           B               NaN  
8623           G  ✔️ [True]    NaN  
8624           C  ✔️ [True]    NaN  
8625           J               NaN  

[8626 rows x 7 columns]

CPU times: user 3min 45s, sys: 7.03 s, total: 3min 52s
Wall time: 30min 42s


(72.86,
 [(Example({'question': 'A 50-year-old nurse who had been fired from his job at ahospital told his attorney, ÒI was fired because of my age, and I want to sue the hospital.Ó Based on this information, the attorney filed an age discrimination complaint against the hospital in federal court. As it turned out, the hospital had hired a 52-year-old man as the nurseÕs replacement, a fact that rendered an age discrimination claim unavailable. The hospital responded tothe complaint by filing a motion for sanctions against thenurseÕs attorney. Is the court likely to grant the hospitalÕs motion?', 'options': {'A': 'No, because sanctions are not proper against the attorney of a represented party.', 'B': 'Yes, because the attorney should have known that age discrimination could not be proven in this case.', 'C': 'No, because the hospital failed to give the attorney the chance to withdraw the complaint in advance of filing the motion with the court.', 'D': "No, because the nurse's complaint

### Optimize Subset + Evaluation

In [9]:
%%time
subset_size = 20
optimizer = dspy.MIPROv2(
    metric=benchmark.metric,
    auto="light",
    num_threads=NUM_THREADS,
    task_model=TASK_MODEL,
    prompt_model=PROMPT_MODEL,
    max_labeled_demos=FEW_SHOTS,
)

optimized_program = optimizer.compile(
    program,
    trainset=trainset[:subset_size],
    valset=valset[:subset_size],
    requires_permission_to_run=False,
)

2025/01/22 12:40:40 INFO dspy.teleprompt.mipro_optimizer_v2: 
RUNNING WITH THE FOLLOWING LIGHT AUTO RUN SETTINGS:
num_trials: 7
minibatch: False
num_candidates: 5
valset size: 20

2025/01/22 12:40:40 INFO dspy.teleprompt.mipro_optimizer_v2: 
==> STEP 1: BOOTSTRAP FEWSHOT EXAMPLES <==
2025/01/22 12:40:40 INFO dspy.teleprompt.mipro_optimizer_v2: These will be used as few-shot example candidates for our program and for creating instructions.

2025/01/22 12:40:40 INFO dspy.teleprompt.mipro_optimizer_v2: Bootstrapping N=5 sets of demonstrations...


Bootstrapping set 1/5
Bootstrapping set 2/5
Bootstrapping set 3/5


 20%|████████████████▍                                                                 | 4/20 [00:09<00:37,  2.34s/it]


Bootstrapped 4 full traces after 4 examples for up to 1 rounds, amounting to 4 attempts.
Bootstrapping set 4/5


 20%|████████████████▍                                                                 | 4/20 [00:08<00:33,  2.07s/it]


...


Average Metric: 16.00 / 20 (80.0%): 100%|█████████████████████████████████████████████| 20/20 [00:14<00:00,  1.35it/s]

2025/01/22 12:43:24 INFO dspy.evaluate.evaluate: Average Metric: 16 / 20 (80.0%)
2025/01/22 12:43:24 INFO dspy.teleprompt.mipro_optimizer_v2: Score: 80.0 with parameters ['Predictor 0: Instruction 0', 'Predictor 0: Few-Shot Set 1'].
2025/01/22 12:43:24 INFO dspy.teleprompt.mipro_optimizer_v2: Scores so far: [70.0, 75.0, 80.0, 80.0, 80.0, 80.0, 80.0]
2025/01/22 12:43:24 INFO dspy.teleprompt.mipro_optimizer_v2: Best score so far: 80.0
2025/01/22 12:43:24 INFO dspy.teleprompt.mipro_optimizer_v2: =======================


2025/01/22 12:43:24 INFO dspy.teleprompt.mipro_optimizer_v2: ===== Trial 7 / 7 =====



Average Metric: 15.00 / 20 (75.0%): 100%|█████████████████████████████████████████████| 20/20 [00:25<00:00,  1.27s/it]

2025/01/22 12:43:49 INFO dspy.evaluate.evaluate: Average Metric: 15 / 20 (75.0%)
2025/01/22 12:43:49 INFO dspy.teleprompt.mipro_optimizer_v2: Score: 75.0 with parameters ['Predictor 0: Instruction 4', 'Predictor 0: Few-Shot Set 4'].
2025/01/22 12:43:49 INFO dspy.teleprompt.mipro_optimizer_v2: Scores so far: [70.0, 75.0, 80.0, 80.0, 80.0, 80.0, 80.0, 75.0]
2025/01/22 12:43:49 INFO dspy.teleprompt.mipro_optimizer_v2: Best score so far: 80.0
2025/01/22 12:43:49 INFO dspy.teleprompt.mipro_optimizer_v2: =======================


2025/01/22 12:43:49 INFO dspy.teleprompt.mipro_optimizer_v2: Returning best identified program with score 80.0!



CPU times: user 2.49 s, sys: 495 ms, total: 2.98 s
Wall time: 3min 9s


In [10]:
%%time
print("BEST PROMPT:\n", optimized_program.predict.signature.instructions)

BEST PROMPT:
 To solve a multiple-choice question, I will carefully read and analyze the question, identify the key concepts and formulas required, and then apply step-by-step reasoning to arrive at the correct answer. I will consider each option and evaluate its validity based on the principles and theories relevant to the subject matter. My response will include a clear explanation of the reasoning process, demonstrating how I arrived at the chosen answer. Please provide the question and options, and I will respond with the reasoning and answer.
CPU times: user 0 ns, sys: 58 μs, total: 58 μs
Wall time: 61.3 μs


In [11]:
%%time
score, results, all_scores = evaluate(
    optimized_program,
    devset=testset,
)

Average Metric: 293.00 / 378 (77.5%):   4%|█▊                                      | 378/8626 [01:28<33:12,  4.14it/s]

2025/01/22 12:46:10 ERROR dspy.utils.parallelizer: Error processing item Example({'question': 'Consider the initial value problem\n$$\n3 u^{\\prime \\prime}-u^{\\prime}+2 u=0, \\quad u(0)=2, \\quad u^{\\prime}(0)=0\n$$\nFor $t>0$ find the first time at which $|u(t)|=10$.', 'options': {'A': '14.1234', 'B': '9.5678', 'C': ' 10.7598', 'D': '16.4321', 'E': '15.6789', 'F': '11.2345', 'G': '12.3456', 'H': '7.6543', 'I': '13.5791', 'J': '8.9876'}, 'answer': ''}) (input_keys={'question', 'options'}): Expected dict_keys(['reasoning', 'answer']) but got dict_keys(['reasoning']). Set `provide_traceback=True` to see the stack trace.


Average Metric: 1756.00 / 2320 (75.7%):  27%|█████████▉                           | 2321/8626 [09:22<27:03,  3.88it/s]

2025/01/22 12:54:04 ERROR dspy.utils.parallelizer: Error processing item Example({'question': "What popular toy is featured in the film 'The Hudsucker Proxy'?", 'options': {'A': 'Lincoln Logs', 'B': 'Beanie Babies', 'C': 'Hot Wheels', 'D': 'Teddy Ruxpin', 'E': 'Slinky', 'F': "Rubik's Cube", 'G': 'Barbie Doll', 'H': 'Yo-Yo', 'I': 'Hula Hoop', 'J': 'Lite Brite'}, 'answer': 'I'}) (input_keys={'question', 'options'}): Expected dict_keys(['reasoning', 'answer']) but got dict_keys(['reasoning']). Set `provide_traceback=True` to see the stack trace.


Average Metric: 1763.00 / 2330 (75.7%):  27%|█████████▉                           | 2331/8626 [09:23<17:32,  5.98it/s]

...

2025/01/22 13:20:13 ERROR dspy.utils.parallelizer: Error processing item Example({'question': 'In a heavily polluted industrialized area in England about 87 percent of the moths of the speciesBistonbetulariaare melanic(dark colored). If the frequency of recessives is 0.13, what is the frequency of the dominant allele leading to melanism? What proportion of the dark colored moths are heterozygous?', 'options': {'A': '0.80, 0.48 or 48%', 'B': '0.55, 0.75 or 75%', 'C': '0.50, 0.50 or 50%', 'D': '0.60, 0.70 or 70%', 'E': '0.64, 0.53 or 53%', 'F': '0.77, 0.30 or 30%', 'G': '0.70, 0.40 or 40%', 'H': '0.87, 0.25 or 25%', 'I': '0.75, 0.60 or 60%', 'J': '0.47, 0.65 or 65%'}, 'answer': 'E'}) (input_keys={'question', 'options'}): Expected dict_keys(['reasoning', 'answer']) but got dict_keys(['reasoning']). Set `provide_traceback=True` to see the stack trace.


Average Metric: 6451.00 / 8591 (75.1%): 100%|█████████████████████████████████████| 8626/8626 [35:32<00:00,  4.05it/s]

2025/01/22 13:20:13 INFO dspy.evaluate.evaluate: Average Metric: 6451.0 / 8626 (74.8%)


question  \
0     7.3-9. Consider the following two groups of women: Group 1 consist...   
1     Find the product of the given polynomials in the given polynomial ...   
2     Classical and neoclassical (marginalist) theorists have usually su...   
3     Calculate the melting point of ice under a pressure of 50 bar. Ass...   
4      Which of the following are the three broad groups of organization...   
...                                                                     ...   
8621         What role does language play in the process of securitization?   
8622                 What is the effective rates for 3% compounded monthly?   
8623  Methane is stored at low temperature inside a tank having a volume...   
8624  The bandwidth of an analog signal is 4kHz. An A/D converter is use...   
8625  The highest levels of learning and performance are usually associa...   

                                                                    options  \
0     {'A': ' $0.2115$', 'B': '$0.3256$', 'C': '$0.1298$', 'D': '$0.2732...   
1     {'A': 'x^2 - 1', 'B': '2x^3 - 4x^2 + 2x', 'C': '8x^3 - 20x^2 + 10x...   
2     {'A': 'Keynes supported a market economy with equal government and...   
3     {'A': '277.3 K', 'B': '276.8 K', 'C': ' 272.8 $\\mathrm{K}$', 'D':...   
4     {'A': 'Organizational size, industry type, and geographical locati...   
...                                                                     ...   
8621  {'A': 'The process of securitization is primarily a non-discursive...   
8622  {'A': '0.027', 'B': '0.0304', 'C': '0.035', 'D': '0.036', 'E': '0....   
8623  {'A': '89,368.79 kJ', 'B': '95,500 kJ', 'C': '120,000 kJ', 'D': '1...   
8624  {'A': '10', 'B': '7', 'C': '4', 'D': '6', 'E': '8', 'F': '12', 'G'...   
8625  {'A': 'constant changes in levels of arousal.', 'B': 'low levels o...   

     example_answer  \
0                 A   
1                 F   
2                 J   
3                     
4                 A   
...             ...   
8621              B   
8622              B   
8623              A   
8624              E   
8625              F   

                                                                  reasoning  \
0     To find a point estimate of $p_1 - p_2$, we first need to calculat...   
1     To find the product of the given polynomials f(x) = 4x - 5 and g(x...   
2     The question requires an understanding of Keynes' economic views, ...   
3     To calculate the melting point of ice under a pressure of 50 bar, ...   
4     The question asks for the three broad groups of organizational cha...   
...                                                                     ...   
8621  The correct answer can be determined by understanding the role of ...   
8622  To find the effective rate for 3% compounded monthly, we use the f...   
8623  To solve this problem, we need to consider the thermodynamic prope...   
8624  To eliminate the aliasing problem, the sampling rate of the A/D co...   
8625  The highest levels of learning and performance are typically achie...   

     pred_answer     metric answer  
0              A  ✔️ [True]    NaN  
1              F  ✔️ [True]    NaN  
2              J  ✔️ [True]    NaN  
3              B               NaN  
4              A  ✔️ [True]    NaN  
...          ...        ...    ...  
8621           B  ✔️ [True]    NaN  
8622           B  ✔️ [True]    NaN  
8623           A  ✔️ [True]    NaN  
8624           E  ✔️ [True]    NaN  
8625           F  ✔️ [True]    NaN  

[8626 rows x 7 columns]

CPU times: user 2min 20s, sys: 6.65 s, total: 2min 27s
Wall time: 35min 33s


## Medium Optimization

In [12]:
%%time
subset_size = 500
optimizer = dspy.MIPROv2(
    metric=benchmark.metric,
    auto="medium",
    num_threads=NUM_THREADS,
    task_model=TASK_MODEL,
    prompt_model=PROMPT_MODEL,
    max_labeled_demos=FEW_SHOTS,
)

optimized_program = optimizer.compile(
    program,
    trainset=trainset[:subset_size],
    valset=valset[:subset_size],
    requires_permission_to_run=False,
)

2025/01/22 13:20:14 INFO dspy.teleprompt.mipro_optimizer_v2: 
RUNNING WITH THE FOLLOWING MEDIUM AUTO RUN SETTINGS:
num_trials: 25
minibatch: True
num_candidates: 19
valset size: 300

2025/01/22 13:20:14 INFO dspy.teleprompt.mipro_optimizer_v2: 
==> STEP 1: BOOTSTRAP FEWSHOT EXAMPLES <==
2025/01/22 13:20:14 INFO dspy.teleprompt.mipro_optimizer_v2: These will be used as few-shot example candidates for our program and for creating instructions.

2025/01/22 13:20:14 INFO dspy.teleprompt.mipro_optimizer_v2: Bootstrapping N=19 sets of demonstrations...


Bootstrapping set 1/19
Bootstrapping set 2/19
Bootstrapping set 3/19


  1%|▋                                                                                | 4/500 [00:09<18:49,  2.28s/it]


Bootstrapped 4 full traces after 4 examples for up to 1 rounds, amounting to 4 attempts.
Bootstrapping set 4/19


  1%|▍                                                                                | 3/500 [00:08<24:50,  3.00s/it]


...

Bootstrapped 1 full traces after 1 examples for up to 1 rounds, amounting to 1 attempts.
Bootstrapping set 19/19


  1%|▍                                                                                | 3/500 [00:11<32:11,  3.89s/it]
2025/01/22 13:22:49 INFO dspy.teleprompt.mipro_optimizer_v2: 
==> STEP 2: PROPOSE INSTRUCTION CANDIDATES <==
2025/01/22 13:22:49 INFO dspy.teleprompt.mipro_optimizer_v2: We will use the few-shot examples from the previous step, a generated dataset summary, a summary of the program code, and a randomly selected prompting tip to propose instructions.


Bootstrapped 3 full traces after 3 examples for up to 1 rounds, amounting to 3 attempts.


2025/01/22 13:23:35 INFO dspy.teleprompt.mipro_optimizer_v2: 
Proposing instructions...

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x7fa34f71e0e0>>
Traceback (most recent call last):
  File "/home/justinai/.conda/envs/prompt-migration/lib/python3.10/site-packages/ipykernel/ipkernel.py", line 775, in _clean_thread_parent_frames
KeyboardInterrupt: 


KeyboardInterrupt: 

In [ ]:
print("BEST PROMPT:\n", optimized_program.predict.signature.instructions)

In [ ]:
print("BEST EXAMPLES:\n", optimized_program.predict.demos)

In [ ]:
%%time
score, results, all_scores = evaluate(
    optimized_program,
    devset=testset[:subset_size],
    display_table=False,
)

In [ ]:
%%time
score, results, all_scores = evaluate(
    optimized_program,
    devset=testset,
)

## Heavy Optimization

In [ ]:
optimizer = dspy.MIPROv2(
    metric=benchmark.metric,
    auto="heavy",
    num_threads=NUM_THREADS,
    task_model=TASK_MODEL,
    prompt_model=PROMPT_MODEL,
    max_labeled_demos=FEW_SHOTS,
)

optimized_program = optimizer.compile(
    program,
    trainset=trainset,
    valset=valset,
)

In [ ]:
print("BEST PROMPT:\n", optimized_program.predict.signature.instructions)

In [ ]:
score, results, all_scores = evaluate(
    optimized_program,
    devset=testset,
    display_table=False,
)